<h1 style align="center"> Mobile Data Analysis </h1>
<hr>
<h5 style align="right"> Work Done by : Marah Baccari & Wissem Bellara  </h3>

scikit-mobility is a library for human mobility analysis in Python. The library allows to:

- represent trajectories and mobility flows with proper data structures, TrajDataFrame and FlowDataFrame.

- manage and manipulate mobility data of various formats (call detail records, GPS data, data from social media, survey data, etc.);

- extract mobility metrics and patterns from data, both at individual and collective level (e.g., length of displacements, characteristic distance, origin-destination matrix, etc.)

- generate synthetic individual trajectories using standard mathematical models (random walk models, exploration and preferential return model, etc.)

- generate synthetic mobility flows using standard migration models (gravity model, radiation model, etc.)

- assess the privacy risk associated with a mobility data set

In [29]:
import pandas as pd
import skmob
import geopandas as gpd
import folium  #Creation des cartes geographiques
from skmob.models.epr import DensityEPR

<h2> I. Trajectory Dataframe</h2>

<h3> 1. Reading and Exploring data </h3> <hr>

This dataset contains check-ins in NYC collected for about 10 month (from 12 April 2012 to 16 February 2013). It contains 227,428 check-ins in New York city. Each check-in is associated with its time stamp, its GPS coordinates and its semantic meaning (represented by fine-grained venue-categories). This dataset is originally used for studying the spatial-temporal regularity of user activity.

In [2]:
df = pd.read_csv('dataset_TSMC2014_NYC.csv')

In [3]:
df.head()

userId                   venueId           venueCategoryId  \
0     470  49bbd6c0f964a520f4531fe3  4bf58dd8d48988d127951735   
1     979  4a43c0aef964a520c6a61fe3  4bf58dd8d48988d1df941735   
2      69  4c5cc7b485a1e21e00d35711  4bf58dd8d48988d103941735   
3     395  4bc7086715a7ef3bef9878da  4bf58dd8d48988d104941735   
4      87  4cf2c5321d18a143951b5cec  4bf58dd8d48988d1cb941735   

         venueCategory   latitude  longitude  timezoneOffset  \
0  Arts & Crafts Store  40.719810 -74.002581            -240   
1               Bridge  40.606800 -74.044170            -240   
2       Home (private)  40.716162 -73.883070            -240   
3       Medical Center  40.745164 -73.982519            -240   
4           Food Truck  40.740104 -73.989658            -240   

                     utcTimestamp  
0  Tue Apr 03 18:00:09 +0000 2012  
1  Tue Apr 03 18:00:25 +0000 2012  
2  Tue Apr 03 18:02:24 +0000 2012  
3  Tue Apr 03 18:02:41 +0000 2012  
4  Tue Apr 03 18:03:00 +0000 2012

In [4]:
df.shape

(227428, 8)

<h3> 2. Creating Trajectory DataFrame</h3> <hr>

In scikit-mobility, each row in the TrajDataFrame represents a point of a trajectory, described by three mandatory fields (aka columns):

- latitude (type: float);
- longitude (type: float);
- datetime (type: date-time).

Additionally, two optional columns can be specified:

- uid (type: string) identifies the object associated with the point of the trajectory. If uid is not present, scikit-mobility assumes that the TrajDataFrame contains trajectories associated with a single moving object;

- tid specifies the identifier of the trajectory to which the point belongs to. If tid is not present, scikit-mobility assumes that all rows in the TrajDataFrame associated with a uid belong to the same trajectory;

Note that, besides the mandatory columns, the user can add to a TrajDataFrame as many columns as they want since the data structures in scikit-mobility inherit all the pandas DataFrame functionalities.

In [5]:
# now create a TrajDataFrame from the pandas DataFrame
tdf = skmob.TrajDataFrame(df, latitude='latitude', longitude='longitude', datetime='utcTimestamp', user_id='userId')
# print the type of the object
type(tdf)

skmob.core.trajectorydataframe.TrajDataFrame

In [6]:
tdf.head()

uid                   venueId           venueCategoryId  \
0  470  49bbd6c0f964a520f4531fe3  4bf58dd8d48988d127951735   
1  979  4a43c0aef964a520c6a61fe3  4bf58dd8d48988d1df941735   
2   69  4c5cc7b485a1e21e00d35711  4bf58dd8d48988d103941735   
3  395  4bc7086715a7ef3bef9878da  4bf58dd8d48988d104941735   
4   87  4cf2c5321d18a143951b5cec  4bf58dd8d48988d1cb941735   

         venueCategory        lat        lng  timezoneOffset  \
0  Arts & Crafts Store  40.719810 -74.002581            -240   
1               Bridge  40.606800 -74.044170            -240   
2       Home (private)  40.716162 -73.883070            -240   
3       Medical Center  40.745164 -73.982519            -240   
4           Food Truck  40.740104 -73.989658            -240   

                   datetime  
0 2012-04-03 18:00:09+00:00  
1 2012-04-03 18:00:25+00:00  
2 2012-04-03 18:02:24+00:00  
3 2012-04-03 18:02:41+00:00  
4 2012-04-03 18:03:00+00:00

In [7]:
tdf.plot_trajectory(max_users=2, start_end_markers=True)

c:\Users\Marah Baccari\AppData\Local\Programs\Python\Python310\lib\site-packages\skmob\core\trajectorydataframe.py:569: UserWarning: If necessary, trajectories will be down-sampled to have at most `max_points` points. To avoid this, specify `max_points=None`.
  return plot.plot_trajectory(self, map_f=map_f, max_users=max_users, max_points=max_points, style_function=style_function,


<h3> 3. Trajectory preprocessing </h3>

As any analytical process, mobility data analysis requires data cleaning and preprocessing steps. The preprocessing module allows the user to perform four main preprocessing steps:

- noise filtering
- stop detection
-  compression

Note that, if a TrajDataFrame contains multiple trajectories from multiple users, the preprocessing methods automatically apply to the single trajectory and, when necessary, to the single moving object.

- <strong>Noise filtering</strong> <br><hr>

In scikit-mobility, the function filter filters out a point if the speed from the previous point is higher than the parameter max_speed, which is by default set to 500km/h.

In [8]:
'''from skmob.preprocessing import filtering
# filter out all points with a speed (in km/h) from the previous point higher than 500 km/h
ftdf = filtering.filter(tdf, max_speed_kmh=500)
print(ftdf.parameters)'''

'from skmob.preprocessing import filtering\n# filter out all points with a speed (in km/h) from the previous point higher than 500 km/h\nftdf = filtering.filter(tdf, max_speed_kmh=500)\nprint(ftdf.parameters)'

- <strong>Stop Detection</strong> <br><hr>

Some points in a trajectory can represent Point-Of-Interests (POIs) such as schools, restaurants, and bars, or they can represent user-specific places such as home and work locations. These points are usually called Stay Points or Stops, and they can be detected in different ways. A common approach is to apply spatial clustering algorithms to cluster trajectory points by looking at their spatial proximity. In scikit-mobility, the stay_locations function, contained in the detection module, finds the stay points visited by a moving object. For instance, to identify the stops where the object spent at least minutes_for_a_stop minutes within a distance spatial_radius_km \time stop_radius_factor, from a given point, we can use the following code:

In [9]:
from skmob.preprocessing import detection
# compute the stops for each individual in the TrajDataFrame
stdf = detection.stay_locations(tdf, stop_radius_factor=0.5, minutes_for_a_stop=20.0, spatial_radius_km=0.2, leaving_time=True)
# print a portion of the detected stops
stdf.shape

(154337, 9)

In [10]:
stdf.head()

uid                   venueId           venueCategoryId  \
0    1  4abc1f51f964a520798620e3  4bf58dd8d48988d1ce941735   
1    1  4d4ac10da0ef54814b6ffff6  4bf58dd8d48988d157941735   
2    1  4db44994cda1c57c82583709  4bf58dd8d48988d1f1931735   
3    1  4a541923f964a52008b31fe3  4bf58dd8d48988d14e941735   
4    1  40f1d480f964a5205b0a1fe3  4bf58dd8d48988d143941735   

           venueCategory        lat        lng  timezoneOffset  \
0     Seafood Restaurant  40.781558 -73.975792            -240   
1    American Restaurant  40.784018 -73.974524            -240   
2  General Entertainment  40.739398 -73.993210            -240   
3    American Restaurant  40.785677 -73.976498            -240   
4         Breakfast Spot  40.719929 -74.008532            -240   

                   datetime          leaving_datetime  
0 2012-04-04 23:31:31+00:00 2012-04-07 17:42:24+00:00  
1 2012-04-07 17:42:24+00:00 2012-04-08 18:20:29+00:00  
2 2012-04-08 18:20:29+00:00 2012-04-08 20:02:10+00:00  
3 2012-04-08 20:02:10+00:00 2012-04-09 16:20:52+00:00  
4 2012-04-09 16:20:52+00:00 2012-04-10 00:24:31+00:00

In [11]:
print('Points of the original trajectory:\t%s'%len(tdf))
print('Points of stops:\t\t\t%s'%len(stdf))

Points of the original trajectory:	227428
Points of stops:			154337


In [12]:
m = stdf.plot_trajectory(max_users=1, start_end_markers=False)
stdf.plot_stops(max_users=1, map_f=m)

c:\Users\Marah Baccari\AppData\Local\Programs\Python\Python310\lib\site-packages\skmob\core\trajectorydataframe.py:569: UserWarning: If necessary, trajectories will be down-sampled to have at most `max_points` points. To avoid this, specify `max_points=None`.
  return plot.plot_trajectory(self, map_f=map_f, max_users=max_users, max_points=max_points, style_function=style_function,


- <strong>Compression</strong> <br><hr>

The goal of trajectory compression is to reduce the number of trajectory points while preserving the structure of the trajectory. This step results in a significant reduction of the number of trajectory points. In scikit-mobility, we can use one of the methods in the compression module under the preprocessing module. For instance, to merge all the points that are closer than 0.2km from each other, we can use the following code:

In [13]:
from skmob.preprocessing import compression
# compress the trajectory using a spatial radius of 0.2 km
ctdf = compression.compress(tdf, spatial_radius_km=0.2)
# print the difference in points between original and filtered TrajDataFrame
print('Points of the original trajectory:\t%s'%len(tdf))
print('Points of the compressed trajectory:\t%s'%len(ctdf))

Points of the original trajectory:	227428
Points of the compressed trajectory:	180294


- <strong>Mobility measures</strong> <br><hr>
Several measures have been proposed in the literature to capture the patterns of human mobility, both at the individual and collective levels. Individual measures summarize the mobility patterns of a single moving object, while collective measures summarize mobility patterns of a population as a whole. scikit-mobility provides a wide set of mobility measures, each implemented as a function that takes in input a TrajDataFrame and outputs a pandas DataFrame. Individual and collective measures are implemented the in skmob.measure.individual and the skmob.measures.collective modules, respectively.

For example, the following code compute the radius of gyration, the jump lengths and the home locations of a TrajDataFrame:

Radius of gyration is a measure that characterizes the dispersion of locations visited by an individual or object in a given period. It provides insights into how much an individual or object explores different areas.

In [14]:
from skmob.measures.individual import jump_lengths, radius_of_gyration, home_location, maximum_distance, number_of_locations
# compute the radius of gyration for each individual
rg_df = radius_of_gyration(tdf)
print(rg_df)

100%|██████████| 1083/1083 [00:01<00:00, 627.49it/s]

       uid  radius_of_gyration
0        1            4.597082
1        2           10.148088
2        3            4.082299
3        4            4.566968
4        5            1.575301
...    ...                 ...
1078  1079            2.706142
1079  1080            4.720708
1080  1081            7.169292
1081  1082            8.182279
1082  1083            1.302178

[1083 rows x 2 columns]


A jump length typically refers to the distance traveled between two consecutive points in a trajectory.

In [15]:
# compute the jump lengths for each individual
jl_df = jump_lengths(tdf.sort_values(by='datetime'))
print(jl_df.head())

  0%|          | 0/1083 [00:00<?, ?it/s]

100%|██████████| 1083/1083 [00:02<00:00, 439.46it/s]

   uid                                       jump_lengths
0    1  [0.2936810890991064, 5.205183093216476, 5.3350...
1    2  [1.357867791299235, 20.745876903367297, 3.4505...
2    3  [5.522448676523457, 2.6448410357146117, 3.2487...
3    4  [0.7568537863892882, 0.0, 0.0, 0.0, 0.0, 1.346...
4    5  [0.3101264033917677, 0.5264088250016002, 3.436...


In [16]:
md_df = maximum_distance(tdf)
print(md_df.head())

  0%|          | 0/1083 [00:00<?, ?it/s]

100%|██████████| 1083/1083 [00:02<00:00, 382.17it/s]

   uid  maximum_distance
0    1         21.944970
1    2         33.191916
2    3         28.169926
3    4         23.208178
4    5          4.418450


In [17]:
nl_df = number_of_locations(tdf)
print(nl_df.head())

  0%|          | 0/1083 [00:00<?, ?it/s]

100%|██████████| 1083/1083 [00:02<00:00, 361.29it/s]

   uid  number_of_locations
0    1                   82
1    2                  118
2    3                   93
3    4                   82
4    5                   34


This function is likely used to identify the home location of an individual based on their mobility data. The home location is a significant point of interest as it represents the place where an individual spends a significant amount of time or returns to regularly.

In [18]:
# compute the home location for each individual
hl_df = home_location(tdf)
print(hl_df.head())

  0%|          | 0/1083 [00:00<?, ?it/s]

100%|██████████| 1083/1083 [00:03<00:00, 289.35it/s]

   uid        lat        lng
0    1  40.776624 -73.979482
1    2  40.624587 -74.142421
2    3  40.725163 -73.992160
3    4  40.816816 -73.941393
4    5  40.726966 -74.038324


In [19]:
import folium
from folium.plugins import HeatMap
# now let's visualize a cloropleth map of the home locations
m = folium.Map(tiles = 'openstreetmap', zoom_start=8, control_scale=True , location=(40.7,-74))
HeatMap( hl_df[['lat', 'lng']].values ).add_to(m)
m

- <strong>Privacy</strong> <br><hr>

Mobility data is sensitive since the movements of individuals can reveal confidential personal information or allow the re-identification of individuals in a database, creating serious privacy risks. 

scikit-mobility provides several attack models, each implemented as a python class. For example in a location attack model, implemented in the LocationAttack class, the malicious adversary knows a certain number of locations visited by an individual, but they do not know the temporal order of the visits. To instantiate a LocationAttack object we can run the following code.

The argument knowledge_length specifies how many locations the malicious adversary knows of each object's movement. The re-identification risk is computed based on the worst possible combination of knowledge_length locations out of all possible combinations of locations.

To assess the re-identification risk associated with a mobility data set, represented as a TrajDataFrame, we specify it as input to the assess_risk method, which returns a pandas DataFrame that contains the uid of each object in the TrajDataFrame and the associated re-identification risk as the column risk (type: float, range: 
 where 0 indicates minimum risk and 1 maximum risk).

In [20]:
from skmob.privacy import attacks
at = attacks.LocationAttack(knowledge_length=2)
#tdf_risk = at.assess_risk(tdf)

Since risk assessment may be time-consuming for more massive datasets, scikit-mobility provides the option to focus only on a subset of the objects with the argument targets. For example, in the following code, we compute the re-identification risk for the object with uid 1 and 2 only:

In [21]:
tdf_risk = at.assess_risk(tdf, targets=[1,2])
print(tdf_risk)

   uid  risk
0    1   1.0
1    2   1.0


<h3>Markov Diary Learner and Generator</h3> 

A Mobility Diary Learner (MDL) is a data-driven algorithm to compute a mobility diary 
from the mobility trajectories of a set of real individuals. We use a Markov model to describe the probability that an individual follows her routine and visits a typical location at the usual time, or she breaks the routine and visits another location. First, MDL translates mobility trajectory data of real individuals into abstract mobility trajectories. Second, it uses the obtained abstract trajectory data to compute the transition probabilities of the Markov model 

In [ ]:
from skmob.models.epr import Ditras
from skmob.models.markov_diary_generator import MarkovDiaryGenerator
from skmob.preprocessing import filtering, compression, detection, clustering

ctdf = compression.compress(tdf)
cstdf = clustering.cluster(stdf)
mdg = MarkovDiaryGenerator()

mdg.fit(cstdf, 2, lid='cluster')
start_time = pd.to_datetime('2012-04-04 23:31:31+00:00')
diary = mdg.generate(100, start_time)
print(diary)

100%|██████████| 2/2 [00:02<00:00,  1.16s/it]

                   datetime  abstract_location
0 2012-04-04 23:31:31+00:00                  0
1 2012-04-06 15:31:31+00:00                  1
2 2012-04-06 16:31:31+00:00                  2
3 2012-04-07 13:31:31+00:00                  3
4 2012-04-07 16:31:31+00:00                  4
5 2012-04-08 13:31:31+00:00                  0


<h3>Density-EPR model</h3> 

In [ ]:
depr = DensityEPR()
start_time = pd.to_datetime('2001/01/01 08:00:00')
end_time = pd.to_datetime('2001/01/14 08:00:00')
tdf = depr.generate(start_date=start_time , end_date=end_time, spatial_tessellation=tessellation, relevance_column='population', n_agents=20, show_progress=True)
print(tdf.head())

  0%|          | 0/20 [00:00<?, ?it/s]c:\Users\Marah Baccari\AppData\Local\Programs\Python\Python310\lib\site-packages\skmob\models\gravity.py:43: RuntimeWarning: divide by zero encountered in power
  return np.power(x, exponent)
100%|██████████| 20/20 [00:01<00:00, 15.84it/s]


   uid                   datetime        lat        lng
0    1 2001-01-01 08:00:00.000000  41.402110 -74.305454
1    1 2001-01-01 08:57:24.410335  40.657677 -73.838633
2    1 2001-01-01 09:19:17.881848  41.402110 -74.305454
3    1 2001-01-01 10:25:17.751744  40.657677 -73.838633
4    1 2001-01-01 11:07:06.994445  40.634238 -73.950237


<h2> II. Flow Dataframe</h2>

<h3>1. Reading Data </h3> 

In [30]:
tessellation = gpd.read_file('NY_counties_2011.geojson').rename(columns={'tile_id': 'tile_ID'})
tessellation.head()

tile_ID  population                                           geometry
0   36019       81716  POLYGON ((-74.00667 44.88602, -74.02739 44.995...
1   36101       99145  POLYGON ((-77.09975 42.27421, -77.09966 42.272...
2   36107       50872  POLYGON ((-76.25015 42.29668, -76.24914 42.302...
3   36059     1346176  POLYGON ((-73.70766 40.72783, -73.70027 40.739...
4   36011       79693  POLYGON ((-76.27907 42.78587, -76.27535 42.780...

<h3>2. Creating a Flow Dataframe </h3> 

In [31]:
# load real flows into a FlowDataFrame
fdf = skmob.FlowDataFrame.from_file("NY_commuting_flows_2011.csv",
                                        tessellation=tessellation,
                                        tile_id='tile_ID',
                                        sep=",")
print(fdf.head())

     flow origin destination
0  121606  36001       36001
1       5  36001       36005
2      29  36001       36007
3      11  36001       36017
4      30  36001       36019


<h3> 3. Trajectory Visualisation </h3>

In [24]:
map2 = folium.Map(location=(40.7,-74), zoom_start = 7)
fdf.plot_tessellation(map2, maxitems=45,geom_col='geometry',popup_features=['tile_ID','population'])

In [25]:
map = folium.Map(location=(40.7,-74) , zoom_start = 7)
fdf.plot_flows(map,flow_color='red' , zoom= 7 , tiles='Stamen Toner')

In [26]:
fdf.plot_tessellation(map, maxitems=45,geom_col='geometry',popup_features=['tile_ID','population'])